In [1]:
import numpy as np
import torch
import pickle
import time
import os
%matplotlib inline
import matplotlib.pyplot as plt
# import gnn

In [2]:
if not os.path.isfile('superpixels.zip'):
    print('downloading..')
    !curl https://www.dropbox.com/s/y2qwa77a0fxem47/superpixels.zip?dl=1 -o superpixels.zip -J -L -k
    !unzip superpixels.zip -d ../
    # !tar -xvf superpixels.zip -C ../
else:
    print('File already downloaded')

downloading..
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100  324M  100  324M    0     0  20.6M      0  0:00:15  0:00:15 --:--:-- 23.2M 0  0:00:45  0:00:02  0:00:43 21.0M
Archive:  superpixels.zip
 extracting: ../superpixels/cifar10_150sp_test.pkl  
 extracting: ../superpixels/cifar10_150sp_train.pkl  
 extracting: ../superpixels/mnist_75sp_test.pkl  
 extracting: ../superpixels/mnist_75sp_train.pkl  


In [3]:

import os
os.chdir('../../') # go to root folder of the project
print(os.getcwd())

/Users/ziangeng/Desktop/Research


In [4]:
import pickle

%load_ext autoreload
%autoreload 2

from superpixels import SuperPixDatasetDGL 

from data import LoadData
from torch.utils.data import DataLoader
from superpixels import SuperPixDataset


In [3]:


DATASET_NAME = 'MNIST'
trainset=[0,1,2,3,4,5]
testset=[6,7,8,9]
way=4
shot=10
task=20
it=0
datasetlist=[]
ftlist=[]
for it in range (task):
    dataset = SuperPixDatasetDGL(DATASET_NAME,trainset,trainset,it,way,task,shot) 
    with open('data/superpixels/MNIST.pkl','wb') as f:
        pickle.dump([dataset.train,dataset.val,dataset.test],f)
    dataset = LoadData(DATASET_NAME) # 54s
    print('train',dataset.train.graph_labels)
    datasetlist.append(dataset)
for it in range (task):
    dataset = SuperPixDatasetDGL(DATASET_NAME,testset,testset,it,way,task,shot) 
    with open('data/superpixels/MNIST.pkl','wb') as f:
        pickle.dump([dataset.train,dataset.val,dataset.test],f)
    dataset = LoadData(DATASET_NAME) # 54s
    print('test',dataset.train.graph_labels)
    ftlist.append(dataset)



NameError: name 'time' is not defined

In [8]:
print(type(datasetlist[0].train.graph_labels))
print(datasetlist[0].train.graph_labels)

<class 'torch.Tensor'>
tensor([3, 2, 4, 2, 0, 3, 2, 4, 2, 3, 0, 0, 2, 0, 4, 3, 4, 3, 4, 4, 4, 3, 0, 2,
        3, 3, 0, 2, 0, 2, 0, 4])


In [1]:
from torch_geometric.datasets import MNISTSuperpixels
import random
from torch.utils.data import random_split,Subset

trainset=[0,1,2,3,4,5]
testset=[6,7,8,9]
# trainset=[0,1,2,3,4,5,6,7,8,9]
# testset=[0,1,2,3,4,5,6,7,8,9]
way=4
shot=10
task=40
SAG = MNISTSuperpixels('data/superpixels/')
# Creates a list containing 5 lists, each of 8 items, all set to 0
indexlist = [[] for y in range(10)] 
# if(SAG[0].y==5):
#     print('hello')
for ind in range (len(SAG)):
    for sa in range(10):
        if(SAG[ind].y==sa):
            indexlist[sa].append(ind)


SAGtrainlist=[]
SAGftlist=[]

for n in range(task):
    train_choice=random.sample(trainset,way)
    ft_choice=random.sample(testset,way)
    tr_indlist=[]
    te_indlist=[]
    ft_indlist=[]
    ftte_indlist=[]
    for t in train_choice:
        tr_indlist=tr_indlist+indexlist[t][n*shot:(n+1)*shot]
        te_indlist=te_indlist+indexlist[t][(len(indexlist[t])-(n+1)*shot):(len(indexlist[t])-n*shot)]
    for f in ft_choice:
#         ft_indlist=ft_indlist+indexlist[f][n*shot:(n+1)*shot]
#         ftte_indlist= ftte_indlist+indexlist[f][(len(indexlist[f])-(n+1)*shot):(len(indexlist[f])-n*shot)]
        ft_indlist=ft_indlist+indexlist[f][(task+n)*shot:(task+n+1)*shot]
        ftte_indlist= ftte_indlist+indexlist[f][(len(indexlist[f])-(task+n+1)*shot):(len(indexlist[f])-(task+n)*shot)]
    sup_qur_tr=[]
    sup_qur_ft=[]
    sup_qur_tr.append(Subset(SAG,tr_indlist))
    sup_qur_tr.append(Subset(SAG,te_indlist))
    sup_qur_ft.append(Subset(SAG,ft_indlist))
    sup_qur_ft.append(Subset(SAG,ftte_indlist))
    SAGtrainlist.append(sup_qur_tr)
    SAGftlist.append(sup_qur_ft)

print('finish')   
    


finish


In [9]:
# from SGAPoolORI import SAGLearnerori

# testori=SAGLearnerori(SAG)
# out,pred,loss,correct=testori()
# print(len(SAGftlist[0][1]))
# for i in range (len(SAGftlist[0][0])):
#     print(SAGftlist[0][1][i].y)



# from HGPORILearner import HGPORILearner

# testoriHGP=HGPORILearner(SAG)
# acc,loss,correct=testoriHGP()
# print(acc)
# print(loss)

In [3]:
# import torch

# from SAGLearner import SAGLearner

# test=SAGLearner(4)



# print(type(test.dataset[0]))
# print(type(test.dataset))
# print('first',test.dataset[0].y)
# print('second',test.dataset[1].y)
# print(test.dataset.num_classes)
# print(test.dataset.num_features)



# pred,out,loss,correct=test(SAGtrainlist[0],'test')
# print('pe',pred)
# print('out',correct)
# # print()
# # test('train')
# for g in range(len(test.modelbn)):
#     print('bn',g,test.modelbn[g])
#     print('para',g,list(test.model.parameters())[g])


In [2]:
from HGPmeta import HGPMeta
from    HGPLearner import HGPLearner
from    copy import deepcopy
import numpy as np
# hgtest=HGPLearner(4)
# net=deepcopy(hgtest)  
# print('done')
# metalist=[0.0001,0.0002,0.0003,0.0005,0.0007,0.001,0.002,0.003,0.005,0.007,0.01,0.02,0.03,0.05]

result=[]
# m=metalist[3]
metalist=[0.01]
m=0.01
step=40
acclist=[]
for s in metalist:
        
    hgtest=HGPMeta(s,m,way,step,step)
    acc,loss=hgtest(SAGtrainlist,SAGtrainlist)
    acctestlist=[]
    acclist.append([s,m,acc,loss])
    for i in range (task):
    
        acctest=hgtest.finetunning(SAGftlist[i],SAGftlist[i])
        acctestlist.append(acctest)
    maccs = np.array(acctestlist).mean(axis=0).astype(np.float16)
    result.append([s,m,maccs])
    
for d in range (len(result)):
    
    print(' way: ',way,' shot: ',shot,' train set step: ',acclist[d][0],' meta: ',acclist[d][1],' acc: ',acclist[d][2],' loss ',acclist[d][3])

for r in range (len(result)):
    
    print(' task: ',task,' ite: ', step,' way: ',way,' shot: ',shot,' step: ',result[r][0],' meta: ',result[r][1],' acc: ',result[r][2])

parameters 0.01 0.01
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 1, 0, 2, 3, 1, 3, 1, 1, 3, 3, 0, 1, 2, 0, 3, 2, 0, 2, 2, 0, 1, 0, 2,
        2, 0, 2, 3, 1, 2, 3, 1, 2, 1, 1, 3, 0, 0, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3

pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 1, 2, 1, 3, 3, 2, 3, 3, 1, 0, 3, 3, 2, 3, 0, 0, 2, 1, 2, 2, 0,
        2, 0, 0, 1, 2, 3, 1, 0, 1, 1, 3, 1, 2, 1, 2, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 1,

pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 1, 0, 0, 1, 2, 3, 3, 1, 2, 2, 1, 3, 3, 1, 0, 0, 3, 2, 0, 0, 2, 1,
        3, 1, 2, 0, 2, 2, 3, 3, 1, 2, 1, 1, 2, 3, 0, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 1,

pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 1, 0, 2, 3, 1, 0, 1, 1, 0, 3, 0, 3, 3, 2, 3, 0, 0, 3, 3, 2, 2, 2, 1,
        1, 2, 0, 1, 2, 3, 3, 1, 3, 1, 0, 2, 2, 0, 1, 2])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 1,

pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 1, 0, 1, 1, 0, 2, 2, 3, 1, 0, 3, 0, 2, 2, 3, 0, 2, 3, 3, 1, 1,
        1, 3, 2, 0, 2, 2, 2, 1, 1, 3, 1, 0, 3, 3, 3, 2])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
        3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
z tensor([0, 1,

...

pred tensor([3, 0, 3, 0, 0, 3, 3, 2, 3, 1, 3, 2, 3, 3, 3, 2, 2, 3, 0, 1, 0, 2, 2, 1,
        1, 2, 0, 0, 3, 0, 0, 2, 3, 3, 3, 2, 3, 0, 3, 0])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([2, 2, 2, 3, 0, 0, 2, 2, 2, 3, 0, 2, 1, 3, 3, 2, 1, 1, 2, 0, 1, 2, 2, 2,
        3, 0, 3, 2, 3, 1, 2, 2, 0, 2, 2, 2, 0, 2, 3, 2])
z tensor([0, 1, 2, 3, 2, 0, 1, 1, 2, 0, 2, 3, 0, 2, 3, 0, 3, 2, 1, 0, 3, 1, 0, 2,
        3, 1, 3, 3, 3, 0, 2, 1, 0, 1, 0, 2, 3, 1, 2, 1])
pred tensor([3, 0, 3, 0, 0, 3, 3, 2, 3, 1, 3, 2, 3, 3, 3, 2, 2, 3, 0, 1, 0, 2, 2, 1,
        1, 2, 0, 0, 3, 0, 0, 2, 3, 3, 3, 2, 3, 0, 3, 0])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([1, 3, 2, 0, 2, 3, 2, 0, 3, 2, 1, 0, 2, 2, 2, 0, 1, 0, 1, 2, 3, 3, 2, 0,
        2, 1, 2, 2, 2, 2, 0, 2, 2, 2, 2, 3, 3, 3, 2, 2])
z tensor([0, 0,

pred tensor([3, 0, 3, 0, 0, 3, 3, 2, 3, 0, 3, 2, 3, 3, 3, 2, 2, 3, 0, 1, 0, 2, 2, 1,
        1, 2, 0, 0, 3, 0, 0, 2, 3, 3, 3, 2, 3, 0, 3, 0])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([2, 3, 3, 2, 2, 0, 2, 1, 2, 3, 2, 3, 3, 2, 0, 2, 2, 2, 0, 0, 1, 2, 2, 3,
        1, 2, 0, 2, 2, 1, 2, 2, 2, 3, 3, 0, 3, 1, 2, 2])
z tensor([0, 0, 1, 0, 2, 2, 1, 2, 3, 3, 2, 1, 1, 0, 2, 2, 0, 3, 0, 2, 1, 3, 3, 2,
        2, 2, 0, 3, 3, 0, 3, 3, 0, 0, 1, 1, 1, 1, 1, 3])
pred tensor([3, 0, 3, 0, 0, 3, 3, 2, 3, 0, 3, 2, 3, 3, 3, 2, 2, 3, 0, 1, 0, 2, 2, 1,
        1, 2, 0, 0, 3, 0, 0, 2, 3, 3, 3, 2, 3, 0, 3, 0])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([0, 0, 2, 3, 2, 0, 2, 2, 3, 2, 1, 3, 2, 2, 2, 2, 2, 3, 2, 2, 2, 2, 2, 0,
        3, 3, 3, 0, 2, 2, 1, 3, 0, 2, 1, 2, 2, 1, 2, 3])
z tensor([0, 0,

pred tensor([3, 0, 0, 3, 0, 2, 3, 2, 3, 3, 2, 2, 3, 3, 0, 2, 2, 2, 0, 2, 2, 2, 3, 0,
        0, 2, 3, 0, 3, 2, 3, 3, 2, 2, 3, 2, 3, 3, 1, 1])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 2, 2, 3, 0, 2, 2, 2, 3, 2, 2, 2, 2, 0, 0, 2, 2, 2, 1, 2, 1, 2, 2, 2,
        2, 1, 0, 1, 2, 2, 2, 0, 2, 3, 0, 2, 2, 2, 3, 2])
z tensor([0, 1, 2, 3, 3, 1, 2, 1, 3, 1, 0, 3, 1, 1, 3, 2, 0, 1, 0, 2, 0, 2, 1, 1,
        0, 0, 3, 0, 1, 0, 2, 2, 0, 3, 3, 2, 3, 2, 3, 2])
pred tensor([3, 0, 0, 3, 0, 2, 3, 2, 3, 3, 2, 2, 3, 3, 0, 2, 2, 2, 0, 2, 2, 2, 3, 0,
        0, 2, 3, 0, 3, 2, 3, 3, 1, 2, 3, 3, 3, 3, 1, 1])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([2, 2, 2, 0, 2, 2, 0, 1, 2, 2, 1, 2, 2, 0, 2, 2, 2, 0, 1, 2, 1, 0, 3, 3,
        2, 2, 2, 2, 3, 0, 2, 3, 2, 2, 2, 2, 2, 2, 2, 3])
z tensor([0, 0,

pred tensor([3, 0, 0, 3, 0, 2, 3, 2, 3, 3, 2, 2, 3, 3, 0, 2, 2, 2, 0, 2, 2, 2, 3, 0,
        0, 2, 3, 0, 3, 2, 3, 3, 2, 2, 3, 3, 3, 3, 1, 1])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([2, 3, 2, 3, 2, 2, 2, 3, 3, 2, 2, 2, 3, 2, 2, 1, 2, 2, 2, 2, 1, 2, 2, 0,
        2, 2, 2, 0, 0, 2, 0, 1, 3, 1, 0, 2, 2, 2, 2, 2])
z tensor([0, 1, 2, 2, 2, 0, 0, 3, 3, 1, 1, 1, 3, 0, 2, 1, 2, 0, 2, 0, 1, 3, 0, 0,
        2, 0, 1, 3, 3, 0, 3, 1, 3, 1, 3, 3, 2, 1, 2, 2])
pred tensor([3, 0, 0, 3, 0, 2, 3, 2, 3, 3, 2, 2, 3, 3, 0, 2, 2, 2, 0, 2, 2, 2, 3, 0,
        0, 2, 3, 0, 3, 2, 3, 3, 2, 2, 3, 3, 3, 3, 1, 1])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([2, 2, 0, 2, 0, 3, 1, 2, 2, 0, 2, 1, 2, 2, 0, 2, 2, 0, 2, 3, 2, 2, 2, 3,
        2, 2, 3, 2, 2, 1, 2, 1, 2, 2, 2, 2, 2, 3, 0, 2])
z tensor([0, 1,

pred tensor([3, 0, 0, 3, 0, 2, 3, 2, 3, 3, 2, 2, 3, 3, 0, 2, 2, 2, 0, 2, 2, 2, 3, 0,
        0, 2, 3, 0, 3, 2, 0, 3, 1, 2, 3, 3, 0, 3, 1, 1])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 2, 0, 0, 2, 2, 0, 0, 2, 2, 2, 2, 3, 0, 2, 2, 1, 2, 2, 2, 1, 2, 3, 2,
        2, 1, 2, 2, 2, 3, 2, 2, 3, 2, 2, 1, 2, 0, 2, 2])
z tensor([0, 1, 2, 3, 2, 0, 1, 3, 1, 2, 1, 2, 3, 3, 1, 1, 0, 2, 0, 2, 0, 2, 3, 1,
        2, 0, 3, 0, 2, 3, 1, 2, 3, 3, 0, 0, 0, 3, 1, 1])
pred tensor([0, 0, 0, 3, 0, 2, 3, 2, 3, 3, 2, 2, 3, 3, 0, 2, 2, 2, 0, 2, 2, 2, 3, 0,
        0, 2, 3, 0, 3, 2, 0, 3, 1, 2, 3, 3, 0, 3, 1, 1])
z tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])
pred tensor([3, 0, 2, 3, 2, 2, 1, 2, 0, 2, 3, 3, 2, 2, 2, 2, 2, 2, 0, 1, 2, 2, 2, 1,
        2, 2, 2, 2, 2, 2, 2, 2, 0, 1, 3, 0, 2, 2, 2, 0])
z tensor([0, 1,

In [ ]:
from SGAmeta import SGAMeta


    
metalist=[0.0001,0.0002,0.0003,0.0005,0.0007,0.001,0.002,0.003,0.005,0.007,0.01,0.02,0.03,0.05]

result=[]
# m=metalist[3]
metalist=[5]
m=0.0005
acclist=[]
for s in metalist:
        
    sgtest=SGAMeta(s,m,way)
    acc,loss=sgtest(SAGtrainlist,SAGtrainlist)
    acctestlist=[]
    acclist.append([s,m,acc,loss])
    for i in range (task):
    
        acctest=sgtest.finetunning(SAGftlist[i],SAGftlist[i])
        acctestlist.append(acctest)
    maccs = np.array(acctestlist).mean(axis=0).astype(np.float16)
    result.append([s,m,maccs])
    
for d in range (len(result)):
    
    print(' way: ',way,' shot: ',shot,' train set step: ',acclist[d][0],' meta: ',acclist[d][1],' acc: ',acclist[d][2],' loss ',acclist[d][3])

for r in range (len(result)):
    
    print(' way: ',way,' shot: ',shot,' step: ',result[r][0],' meta: ',result[r][1],' acc: ',result[r][2])
    
  

In [11]:
from meta import Meta
support=[]
query=[]
supporty=[]
queryy=[]

for it in range (task):
    support.append(datasetlist[it])
    query.append(datasetlist[it])

    supporty.append(datasetlist[it].train.graph_labels)

    queryy.append(datasetlist[it].test.graph_labels)

    
metalist=[0.0001,0.0002,0.0005,0.0007,0.001,0.002,0.005,0.007,0.01,0.0003,0.003,0.006]
# metalist=[0.0001,0.0005,0.0007,0.001,0.005,0.007,0.01]
# metalist=[0.0007]
result=[]
# m=metalist[11]
m=0.0007
acclist=[]
for s in metalist:
        
    test=Meta(s,m,way)
    acc,loss=test(support,supporty,query,queryy)
    acctestlist=[]
    acclist.append([s,m,acc,loss])
    for i in range (task):
    
        acctest=test.finetunning(ftlist[i], ftlist[i].train.graph_labels, ftlist[i], ftlist[i].test.graph_labels)
        acctestlist.append(acctest)
    maccs = np.array(acctestlist).mean(axis=0).astype(np.float16)
    result.append([s,m,maccs])
    
for d in range (len(result)):
    
    print(' way: ',way,' shot: ',shot,' train set step: ',acclist[d][0],' meta: ',acclist[d][1],' acc: ',acclist[d][2])

for r in range (len(result)):
    
    print(' way: ',way,' shot: ',shot,' step: ',result[r][0],' meta: ',result[r][1],' acc: ',result[r][2])
    
    

parameters 0.0001 0.0007


pred tensor([[ -27.4681,  -37.4563,   -6.4286,  -59.3639,   -9.6936,  -20.0562,
          -15.9069,  -59.1448,  -50.7052,  -49.9213],
        [   2.3345,    6.2851,   29.9758,  -10.9925,  -48.2541,  -29.3841,
          -55.7767,   -4.0772,  -43.6614,  -56.3338],
        [   4.0134,  -38.1618,    5.9042,  -48.1722,   26.5096,   -6.5140,
          -35.0588,  -35.3664,  -30.8195,  -62.5567],
        [ -12.7375,  -50.7557,    1.4178,  -61.0120,   -9.2549,  -19.1167,
            4.7424,  -82.8827,  -49.1980,  -34.1208],
        [   1.3187,  -25.9934,   36.5071,  -37.8217,  -45.7751,  -48.5316,
           13.2788,  -29.5000,  -55.3647,  -43.8863],
        [ -15.0631,  -34.0531,   -9.3892,  -92.8669,   35.8934,   -3.2155,
          -19.4121,  -92.0101,  -19.3827,  -52.7821],
        [   4.3376,  -29.4709,   30.1318,  -26.9460,   -4.7099,  -42.9216,
           -0.5373,  -18.4000,  -58.4216,  -42.4781],
        [  -7.4882,    6.5262,   26.3419,  -20.9879,  -57.3043,  -44.1463,
           -5.943

pred tensor([[ -13.8087,  -10.7579,    3.0187,  -22.5940,    2.5548,   -6.3104,
          -44.0465,  -15.4099,  -36.4008,  -30.4952],
        [  -0.1880,   -8.4738,   12.3299,    6.1342,  -10.6022,  -13.6947,
          -50.8835,   -4.3790,  -57.5310,  -53.2740],
        [  -2.9340,   40.0006,   31.5954,   42.9768,  -78.5170,    1.8699,
          -51.4938,   14.8410,  -25.5153,  -62.6062],
        [  -2.7772,  -50.7794,   -7.1126,  -81.3920,  -17.3706,  -22.9474,
            1.7947, -102.1477,  -43.3505,  -46.6933],
        [  -9.4285,  -61.3150,    0.7184,  -90.3380,   11.1096,  -22.7588,
            6.2282,  -79.0584,  -39.2155,  -44.4785],
        [   9.1354,  -31.7006,   21.4528,  -47.8680,  -21.5983,  -35.9711,
           -3.7945,  -35.9803,  -75.2456,  -43.6774],
        [  15.8027,  -35.0277,   19.2091,  -53.3034,  -45.0614,  -63.9917,
           -6.3147,  -45.6241,  -88.9750,  -51.5572],
        [   8.9526,  -25.6109,    9.6993,  -34.0312,  -44.4962,  -19.3063,
            6.792

pred tensor([[ -6.7484, -13.2419, -24.3073, -21.6317,  -2.6939,  -9.3158, -43.0880,
         -22.8864, -35.4038, -22.4702],
        [ 23.1683,  -4.9464, -10.1698,  11.9903, -14.8190, -13.4685, -39.0296,
         -10.2132, -60.0340, -42.4102],
        [ 24.3151,  32.5864,  -9.6980,  56.3365, -91.4380,  -2.7002, -33.9704,
           8.3055, -30.9244, -44.8089],
        [ -9.1685, -44.6594,   0.1228, -77.2832,   0.1045, -18.3431, -17.2111,
         -97.2727, -43.6067, -58.2696],
        [-20.9245, -56.9257,   8.0830, -82.2789,  26.2845, -19.2281,  -8.6851,
         -69.4557, -34.5738, -55.4797],
        [ 20.4920, -34.8601,   8.7702, -42.6486, -16.2964, -32.0110,  -4.6351,
         -38.4489, -74.2211, -45.1076],
        [ 26.2738, -44.1800,  -2.6860, -47.0705, -49.8701, -63.5219,  -7.6091,
         -43.7708, -89.1270, -46.4915],
        [ 29.5137, -27.4767, -15.7082, -20.4328, -55.3798, -20.2485,   8.0350,
          -9.9289, -74.4750,  -9.9670],
        [-17.0295, -15.3024,  14.4714, -26.

pred tensor([[ -31.7643,  -22.2315,    3.0284,  -68.4673,   21.9440,   -7.6260,
          -12.4952,  -81.2296,  -30.3783,  -48.5331],
        [  15.4755,  -46.4577,  -11.3658,   -6.1110,  -28.7966,  -24.2155,
           10.0400,  -21.9622,  -56.2953,  -17.0599],
        [  36.5908,  -23.1986,  -29.8998,  -25.4519,  -29.2023,  -20.1224,
          -52.8134,   -4.5756,  -56.9099,  -47.5579],
        [  32.7674,    2.6046,   -8.2673,   -0.7997,  -61.9521,  -35.7935,
          -47.2357,   -7.1186,  -43.8812,  -47.3234],
        [  -9.5056,  -20.3838,   25.4814,  -13.5448,   11.2074,   -7.5189,
          -30.9334,  -22.5230,  -21.9934,  -57.9324],
        [  -3.1374,  -21.7075,   15.2917,  -35.6839,  -19.7214,  -49.5596,
          -17.5675,  -58.2281,  -60.6157,  -64.4405],
        [  -2.4883,  -31.9375,    9.5113,  -49.6676,   17.9619,  -28.2354,
          -18.7950,  -42.8640,  -40.9810,  -56.6388],
        [  31.1871,  -16.8650,  -19.6946,    7.7673,  -63.2635,  -14.0477,
          -37.809

...

pred tensor([[-30.4818, -28.0793, -73.9327, -41.5081, -35.1336, -11.6469, -15.7548,
           3.4103, -11.5129,  -2.3808],
        [-41.3454, -39.4486, -82.5211, -14.0803, -47.5428, -25.0640, -36.1764,
           2.5375, -35.3773,  18.2798],
        [-35.6580, -51.2019, -65.7319, -50.6641, -25.8321, -36.3451, -15.2955,
         -33.4889, -22.0988,  20.1375],
        [-32.1632, -32.4420, -60.5962, -44.5378, -34.7707, -22.9092, -12.2393,
           8.2671, -35.0838, -10.8334],
        [-37.1348, -30.9622, -51.8675, -41.1390, -44.2531, -19.9053, -28.6354,
         -24.7644,  16.9295,  -4.1987],
        [-34.0625, -44.8206, -70.0819, -34.7947, -41.6738, -29.7572, -26.1389,
         -22.6431, -14.2868,  28.6979],
        [-28.9289, -44.9494, -83.6822, -23.7536, -40.9384, -32.8820, -33.9276,
         -20.7738, -30.0940,  38.3919],
        [-18.0001, -26.8343, -47.9141, -42.8093, -32.0539, -43.8925,  13.6537,
          -3.5452, -12.3135,  12.0870],
        [-63.3141, -38.6962, -76.4417, -39.

pred tensor([[  9.3385, -65.2112, -10.1476, -17.5276, -14.2556,  -2.2457, -20.8631,
         -21.6541,  25.6403,  58.5615],
        [-30.9155,  -9.2825, -94.9289, -33.1968, -42.3830,  -7.2887, -13.0804,
          32.3831, -35.8235, -40.5473],
        [-38.0372, -24.3496, -71.5222, -41.3197, -34.8640, -32.5692, -28.7283,
         -15.3784, -11.0357, -45.8562],
        [-39.4172, -36.4795, -58.3844, -36.4530, -32.2972, -45.5774,  37.0546,
          -1.5047,  -3.4508,  -2.0091],
        [-36.4391, -41.4537, -61.9911, -38.0812, -56.5131, -19.3004, -49.1758,
          -2.2169,   2.8748, -20.8646],
        [-65.7482, -29.9878, -55.6067, -44.4321,  -3.8335, -39.3684,  34.2749,
         -51.0515,  41.3372, -14.6287],
        [-33.0893, -31.4831, -75.6935, -49.3024, -57.1545, -12.1373, -28.6624,
           8.3820,   0.4167, -32.7430],
        [-42.7843, -20.4988, -91.8585, -37.2717, -31.7685, -19.5160,  -2.3847,
          25.9366, -22.1995, -31.2698],
        [-54.8786, -43.4244, -65.5343, -29.

pred tensor([[-14.5261, -27.9527, -43.7501, -39.3301, -30.6408, -45.6115,  22.1216,
           1.2231,  -6.0670,  -9.5132],
        [-66.5460, -40.9517, -76.7511, -40.8176, -13.3382, -32.3989,  24.9209,
         -24.8704, -13.2107, -20.6521],
        [-48.7658, -27.3016, -83.0466, -38.7779, -16.5726, -43.5835,  10.7909,
         -25.4616,   2.8524,   3.4157],
        [-19.2529, -33.0484, -75.2248, -26.7409, -43.0574, -18.3148, -28.8370,
          25.2860, -28.7723, -34.3742],
        [-35.3382, -31.0674, -61.1833, -45.7087, -32.5274, -22.1062,  -3.3885,
          20.7736, -28.1802, -40.7755],
        [-41.1593, -44.2346, -74.4676, -25.7667, -45.4212, -21.6352, -37.6726,
           9.2828, -14.0537,  -7.9667],
        [-51.0104, -53.0706, -61.3014, -43.5664, -27.2426, -23.3740, -18.1340,
         -22.4063,  21.7409, -15.5345],
        [-41.8914, -32.3961, -54.7962, -51.0557, -50.0985, -13.6055,   5.3654,
          -5.5121,  31.3035, -37.1580],
        [-25.7399, -30.1059, -74.3156, -40.

pred tensor([[  1.0872, -71.3907, -15.6102, -25.6849, -21.9760,  -4.5751, -12.2464,
         -30.9631,  21.6898,  69.9244],
        [-30.8115, -11.2493, -92.6289, -30.3400, -43.1743,  -5.6209, -20.1374,
          24.7535, -43.8401, -14.4251],
        [-35.8607, -26.6809, -70.6937, -40.0837, -35.9488, -33.3073, -33.5851,
         -26.1561, -22.5554, -12.3628],
        [-38.3512, -31.5283, -58.1116, -38.0179, -30.3546, -43.9697,  23.3246,
          -2.5699, -11.9052,  12.4350],
        [-35.2910, -45.1902, -65.4724, -37.0244, -58.2289, -26.7954, -49.9166,
         -21.8166, -15.7732,  22.7462],
        [-62.8084, -23.3232, -55.0578, -46.1767,  -1.7989, -35.8411,  11.9774,
         -44.1825,  38.2745,  -7.2576],
        [-32.8745, -30.0451, -77.7715, -51.2806, -54.0815, -16.5260, -34.7671,
          -0.7682, -11.9096,  -6.5416],
        [-44.8707, -21.7981, -90.4712, -35.5427, -32.0265, -15.4632,  -8.5508,
          18.0414, -28.5138,  -3.5827],
        [-54.4201, -43.3265, -66.3540, -28.

KeyboardInterrupt: 

In [44]:
#### import tensorflow as tf
import torch



# compute the second order derivative w.r.t. each parameter
def sec_grad(loss,parameter):
    loss_grads = torch.autograd.grad(loss, parameter, create_graph=True)
    d2loss = []
    print(len(loss_grads))
    for param, grd in zip(parameter, loss_grads):
        for idx in range(len(loss_grads)):
            drv = torch.autograd.grad(grd[idx], param[idx], create_graph=True)
            d2loss.append(drv)
    return drv
           


# grad = torch.autograd.grad(loss,self.net.modelbn)


x_train_tensor=torch.FloatTensor([0.01])
# testensor=torch.nn.Parameter(testensor)
# # testensor=testensor+testensor
# print(type(testensor))

a = torch.nn.Parameter(torch.randn(1, requires_grad=True, dtype=torch.float))
b = torch.nn.Parameter(torch.randn(1, requires_grad=True, dtype=torch.float))
c = a + 1
# d = torch.nn.Parameter(c, requires_grad=True)
d=c

# print(x_train_tensor)
for epoch in range(2):
    yhat = d + b * x_train_tensor
    error = x_train_tensor - yhat
    
    
    loss = (error ** 2).mean()
    grad = sec_grad(loss,c)
    print('grad',grad)
#     loss.backward()
#     print('a',a.grad)
#     print('b',b.grad)
#     b.grad.zero_()
#     print('c',c.grad)
#     print('d',d.grad)
#     d.grad.zero_()
# print(x_train_tensor)  
for epoch in range(2):
    yhat = d + b * x_train_tensor
    
    error = x_train_tensor - yhat
    loss = (error ** 2).mean()
    print('y',loss)
    loss.backward()
    print('a',a.grad)
#     a.grad.zero_()
    print('b',b.grad)
    b.grad.zero_()
    print('c',c.grad)
#     c.grad.zero_()
    print('d',d.grad)
    d.grad.zero_()

1


IndexError: invalid index of a 0-dim tensor. Use `tensor.item()` in Python or `tensor.item<T>()` in C++ to convert a 0-dim tensor to a number

In [47]:
import torch
from torch import Tensor
from torch.autograd import Variable
from torch.autograd import grad
from torch import nn

# some toy data
x = Variable(Tensor([4., 2.]), requires_grad=False)
y = Variable(Tensor([1.]), requires_grad=False)

# linear model and squared difference loss
model = nn.Linear(2, 1)
loss = torch.sum((y - model(x))**2)
print('lossd1',loss)
# instead of using loss.backward(), use torch.autograd.grad() to compute gradients
loss_grads = grad(loss, model.parameters(), create_graph=True)
print('lossd2',loss_grads[0])
# compute the second order derivative w.r.t. each parameter
d2loss = []
for param, grd in zip(model.parameters(), loss_grads):
    for idx in range(len(loss_grads)):
        drv = grad(grd[idx], param[idx], create_graph=True)
        d2loss.append(drv)
        print(param, drv)

lossd1 tensor(0.1069, grad_fn=<SumBackward0>)
lossd2 tensor([[-2.6156, -1.3078]], grad_fn=<TBackward>)


RuntimeError: grad can be implicitly created only for scalar outputs

In [85]:

class Net(torch.nn.Module):
    def __init__(self, iS):
        super(Net, self).__init__()
        self.layer = torch.nn.Linear(iS, 1)
    def forward(self, inputs):
        outputs = self.layer(inputs)
        outputs = torch.exp(outputs)
        return outputs.mean()
net = Net(10)
inputs = torch.rand(256, 10)
loss = net(inputs)
first_order_grads = torch.autograd.grad(loss, net.parameters(), retain_graph=True,create_graph=True)
first_order_grads = torch.cat([x.view(-1) for x in first_order_grads])
second_order_grads = []
s

# print(first_order_grads )
print(second_order_grads)
result=second_order_grads[0][0][0]
result[1]=second_order_grads[1][0][0][1]
result[2]=second_order_grads[2][0][0][2]
result[3]=second_order_grads[3][0][0][3]
print(result)

print(second_order_grads[2][0][0][2])



[(tensor([[0.2775, 0.2121, 0.2123, 0.2158, 0.2048, 0.2153, 0.1988, 0.1910, 0.2206,
         0.2140]]), tensor([0.4192])), (tensor([[0.2121, 0.2891, 0.2125, 0.2174, 0.2065, 0.2175, 0.2185, 0.1960, 0.2304,
         0.2140]]), tensor([0.4313])), (tensor([[0.2123, 0.2125, 0.2794, 0.2175, 0.2067, 0.2004, 0.1997, 0.1888, 0.2134,
         0.2063]]), tensor([0.4159])), (tensor([[0.2158, 0.2174, 0.2175, 0.2929, 0.2133, 0.2171, 0.2176, 0.2010, 0.2309,
         0.2082]]), tensor([0.4336])), (tensor([[0.2048, 0.2065, 0.2067, 0.2133, 0.2607, 0.2071, 0.1949, 0.1850, 0.2189,
         0.1969]]), tensor([0.4018])), (tensor([[0.2153, 0.2175, 0.2004, 0.2171, 0.2071, 0.2821, 0.2013, 0.1911, 0.2225,
         0.2170]]), tensor([0.4191])), (tensor([[0.1988, 0.2185, 0.1997, 0.2176, 0.1949, 0.2013, 0.2736, 0.1983, 0.2181,
         0.2009]]), tensor([0.4115])), (tensor([[0.1910, 0.1960, 0.1888, 0.2010, 0.1850, 0.1911, 0.1983, 0.2391, 0.2028,
         0.1841]]), tensor([0.3860])), (tensor([[0.2206, 0.2304, 0.213

In [15]:
grads = {}
def save_grad(name):
    def hook(grad):
        grads[name] = grad
    return hook
a = torch.nn.Parameter(torch.randn(1, requires_grad=True, dtype=torch.float))
b = torch.nn.Parameter(torch.randn(1, requires_grad=True, dtype=torch.float))
c = a + 1
# c.register_hook(save_grad(0))
# a.register_hook(save_grad(1))

# c.retain_grad()
# grad = torch.autograd.grad(loss, c,allow_unused=True)
d = c
# d = torch.nn.Parameter(c, requires_grad=True,)
for epoch in range(2):
    yhat = d + b * x_train_tensor
    error = x_train_tensor - yhat
    loss = (error ** 2).mean()
    grad = torch.autograd.grad(loss, c,allow_unused=True)
#     loss.backward()
    print('grad',grad)
    print('a',a.grad)
    print('b',b.grad)
    print('c',c.grad)
    print('d',d.grad)
    print('cg2',grads)
    
for epoch in range(2):
    yhat = d + b * x_train_tensor
    
    error = x_train_tensor - yhat
    loss = (error ** 2).mean()
    print('y',loss)
    loss.backward()
    print('a',a.grad)
#     a.grad.zero_()
    print('b',b.grad)
    b.grad.zero_()
    print('c',c.grad)
#     c.grad.zero_()
    print('d',d.grad)
    d.grad.zero_()

cg1 {}
grad (tensor([3.4687]),)
a None
b None
c None
d None
cg2 {}
grad (tensor([3.4687]),)
a None
b None
c None
d None
cg2 {}


In [ ]:
from    torch.nn import functional as F
from    torch import nn
w = torch.randn(8,4,3,3)
x= tf.constant([1,2,0,1,2])
py= tf.constant([[0.1,0.4,0.5],[0.1,0.4,0.5],[0.1,0.4,0.5],[0.1,0.4,0.5],[0.1,0.4,0.5]])
print(x)
# vars = nn.ParameterList()
# vars.append(w)

# b = torch.randn(8,4,3,3)
lm= nn.Linear(4, 6)
y=lm(x)
# y.backward()
criterion = nn.CrossEntropyLoss()
print(y,py)
loss = criterion(py,y)


# print(y)
# print(x.grad)
# F.conv2d(inputs, filters, padding=1)
# y=torch.nn.Conv2d(3, 18, kernel_size=3, stride=1, padding=1)                
# y = F.conv2d(x, w,padding=1)
# y.backward()
# loss_q = F.cross_entropy(y, y)


In [ ]:
# import torch
# import torch.nn as nn
# from torch.optim import Adam

# class NN_Network(nn.Module):
#     def __init__(self,in_dim,hid,out_dim):
#         super(NN_Network, self).__init__()
#         self.linear1 = nn.Linear(in_dim,hid)
#         self.linear2 = nn.Linear(hid,out_dim)
#         self.linear1.weight = torch.nn.Parameter(torch.zeros(in_dim,hid))
#         self.linear1.bias = torch.nn.Parameter(torch.zeros(hid))
#         self.linear2.weight = torch.nn.Parameter(torch.zeros(in_dim,hid))
#         self.linear2.bias = torch.nn.Parameter(torch.ones(hid))
#         print('p1',self.linear1.weight)
#         print('p1',self.linear1.bias)
#         print('p3',self.linear2.weight)
#         print('p1',self.linear2.bias)
#     def forward(self, input_array):
#         h = self.linear1(input_array)
#         y_pred = self.linear2(h)
#         return y_pred

# in_d = 5
# hidn = 2
# out_d = 3
# net = NN_Network(in_d, hidn, out_d)
# print('check',list(net.parameters()))
# for param in net.parameters():
#     print(type(param.data), param.size())

In [ ]:
from    learner import Learner
test=Learner(4)
ori=test.parameters()
# print('onigi',test.vars[1].weight)
loss1,pred1,acc1=test(datasetlist[0],'train',init=True)
loss2,pred2,acc2=test(datasetlist[0],'test',init=True)


# test(datasetlist[1],'train')
# test(datasetlist[2],'train')
# print('aft',aft.weight)
# print('onigi',test.vars[1].weight)
print('acc1',acc1)
print('testloss',loss1)
print('labelout1',datasetlist[0].train.graph_labels)
print('pred',pred1)
print('acc2',acc2)
# print('score',escore)
# print('label',elabel)

print('testloss2',loss2)
# print('score',escore)
# print('label',elabel)
print('labelout2',datasetlist[0].test.graph_labels)
print('pred2',pred2)
# print(test.parameters())
# print(type(elabel))
# print(type(pred))

In [ ]:
x = torch.ones(2, 2, requires_grad=True)
y = 0.01*x + 2
print(y)
# z = y * y * 3
# out = z.mean()
# f=out-2
y.backward()
print(x.grad)

In [ ]:
from    torch import nn
n = 70 # num of points

# x is a tensor
x = torch.linspace(0, 10, steps=n)
k = torch.tensor(2.5)

# y is a tensor
y = k*x + 5*torch.rand(n)

# loss function
def mse(y_hat, y): return ((y_hat-y)**2).mean()

a = torch.tensor(-1., requires_grad=True)
a = nn.Parameter(a)
print('ori',a)
y_hat = a*x

loss = mse(y_hat, y) 
# print(loss) 
loss.backward(a)
# print(a.grad)
a.grad.zero_()
print('new',a)
lr = 0.1
a = a - lr * a.grad

In [ ]:
# def plot_histo_graphs(dataset, title):
#     # histogram of graph sizes
#     graph_sizes = []
#     for graph in dataset:
#         graph_sizes.append(graph[0].number_of_nodes())
#         #graph_sizes.append(graph[0].number_of_edges())
#     plt.figure(1)
#     plt.hist(graph_sizes, bins=20)
#     plt.title(title)
#     plt.show()
#     graph_sizes = torch.Tensor(graph_sizes)
#     print('nb/min/max :',len(graph_sizes),graph_sizes.min().long().item(),graph_sizes.max().long().item())
    
# plot_histo_graphs(dataset.train,'trainset')
# plot_histo_graphs(dataset.val,'valset')
# plot_histo_graphs(dataset.test,'testset')

In [ ]:
# print(len(dataset.train))
# print(len(dataset.val))
# print(len(dataset.test))

# print(dataset.train[0])
# print(dataset.val[0])
# print(dataset.test[0])

In [ ]:
start = time.time()

with open('data/superpixels/MNIST.pkl','wb') as f:
        pickle.dump([dataset.train,dataset.val,dataset.test],f)
        
print('Time (sec):',time.time() - start) # 38s

In [ ]:
DATASET_NAME = 'MNIST'
dataset = LoadData(DATASET_NAME) # 54s
trainset, valset, testset = dataset.train, dataset.val, dataset.test
print(dataset.train.graph_labels)

In [ ]:
from    learner import Learner
test=Learner()

loss=test(dataset)
print('loss',loss)
# from sklearn import preprocessing 

# label_encoder = preprocessing.LabelEncoder() 

# check = [4,7,7,6,4,4,7,6,7,4,4,4]
# trans=torch.tensor(label_encoder.fit(range(10)))
# trans=label_encoder.fit([4,6,7])
# change=trans.transform(check)
# print(check)
# print(change)

In [ ]:
# # print(test_acc)
# # print(train_acc)
from    torch.nn import functional as F
input = torch.randn(15, 4, requires_grad=True)
# each element in target has to have 0 <= value < C
target = torch.tensor([1, 0, 3,1,1,3,1,3,1,1,3,1,3,1,3])
output = F.nll_loss(F.log_softmax(input), target)
output.backward()
print(input)
print(target)
print(output)


In [ ]:
start = time.time()
input = torch.randn(20, 4, requires_grad=True)
# each element in target has to have 0 <= value < C
target = torch.tensor([4,4,0,4,1,4,0,1,4,0,4,1,4,0,4,1,4,0,4,1])
batch_size = 10
collate = dataset.collate
train_loader = DataLoader(trainset, batch_size=batch_size, shuffle=True, collate_fn=collate)
# for iter, (batch_graphs, batch_labels, batch_snorm_n, batch_snorm_e) in enumerate(train_loader):
#     print(batch_labels)
print('Time (sec):',time.time() - start) # 0.0003s

#### 